## Individual Campaign Finance Contributions from FEC Data

The following Python code does some preliminary exploration of campaign finance data from the Federal Election Committee (FEC) website.  It requires that the following three files be downloaded and unzipped and placed in the specified directories (relative to the notebook)

[Candidate master for 2017-2018](https://www.fec.gov/files/bulk-downloads/2018/cn18.zip) - unzip and place cn.txt in directory fec/cm18/

[Committee master for 2017-2018](https://www.fec.gov/files/bulk-downloads/2018/cm18.zip) - unzip and place cm.txt in directory fec/cn18/

[Contributions by individuals for 2017-2018](https://www.fec.gov/files/bulk-downloads/2018/indiv18.zip) - unzip and place itcont.txt in directory fec/indiv18/

### Load all Individual Contributions and Merge Information from Committee and Candidate Tables.

The individual contribution table is very large.  It will be loaded into object ii and only reloaded if ii doesn't exist.  The following code will create ii if it doesn't exist and output the first row to show all available fields:


In [50]:
import pandas as pd
pd.set_option('display.width', 220)
pd.set_option('max_rows', 200)

year = 2018
try:
    ii
except NameError:
    yr = year % 100
    filepath = "fec/indiv" + str(yr) + "/itcont.txt"
    hdr = pd.read_csv("https://www.fec.gov/files/bulk-downloads/data_dictionaries/indiv_header_file.csv", skiprows=0)
    print("READING "+filepath)
    ii = pd.read_table(filepath, sep='|', header=None, names=hdr)
    print(ii.shape)
    hdr = pd.read_csv("https://www.fec.gov/data/advanced/files/bulk-downloads/data_dictionaries/cm_header_file.csv", skiprows=0)
    cm = pd.read_table("fec/cm" + str(yr) + "/cm.txt", sep='|', header=None, names=hdr.columns)
    hdr = pd.read_csv("https://www.fec.gov/data/advanced/files/bulk-downloads/data_dictionaries/cn_header_file.csv", skiprows=0)
    cn = pd.read_table("fec/cn" + str(yr) + "/cn.txt", sep='|', header=None, names=hdr.columns)
    ii=ii.merge(cm, left_on='CMTE_ID', right_on='CMTE_ID')
    ii=ii.merge(cn, left_on='CAND_ID', right_on='CAND_ID', how='left')
    ii['TRANSACTION_DT'] = ii['TRANSACTION_DT'].fillna(0).astype(int)
    ii['TRANSACTION_DT'] = pd.to_datetime(ii['TRANSACTION_DT'],format='%m%d%Y',errors='coerce')
    ii.rename(columns={'TRANSACTION_DT':'DATE', 'TRANSACTION_AMT':'AMT', 'CAND_PTY_AFFILIATION':'PARTY'}, inplace=True)
    #ii['AMOUNT'] = ii['AMT'].apply(lambda x: '{:,}'.format(x))
print(ii.iloc[0,:])


CMTE_ID                                        C00629618
AMNDT_IND                                              N
RPT_TP                                               TER
TRANSACTION_PGI                                        P
IMAGE_NUM                             201701230300133512
TRANSACTION_TP                                       15C
ENTITY_TP                                            IND
NAME                                       PEREZ, JOHN A
CITY                                         LOS ANGELES
STATE                                                 CA
ZIP_CODE                                           90017
EMPLOYER                                       PRINCIPAL
OCCUPATION                        DOUBLE NICKEL ADVISORS
DATE                                 2017-10-03 00:00:00
AMT                                                   40
OTHER_ID                                       H6CA34245
TRAN_ID                                    SA01251735122
FILE_NUM                       

### Largest Individual Contributions Grouped by the Name, City, and State of the Contributor
The following code aggregates the individual contributions by the name, city, and state of the contributor to get an initial estimate of the total contributions made by each contributor.  This is only an initial estimate because, if a single contributor should vary or misspell any of these items, those contributions will be grouped separately.  For example, note that items 3, 10, 37, 40, and 43 all appear to be for the same contributor, Richard Uihlein of Lake Forest, IL.  The names listed are UIHLEIN, RICHARD; UIHLEIN, RICHARD E.; UIHLEIN, RICHARD E.; UIHLEIN, RICHARD and UIHLEIN, RICHARD E. MR.  Of these, only the first and fourth and the second and third appear to be the same.  However, the first (item 3) and fourth (item 40) differ in that the first state is IL and the second state is IN.  Then, the second (item 10) and third (item 37) differ because the latter item misspells the city as LAKE FORST.  In any event, the final total following the table shows that over $1.9 billion has already been contributed to federal candidates, PACs, and other committees.

In [51]:
jj = ii.groupby(['NAME','CITY','STATE'])['AMT'].agg(['sum'])
jj = jj.reset_index(level=['NAME','CITY','STATE'])
jj.columns = ['NAME','CITY','STATE','AMT']
jj['AMOUNT'] = jj['AMT'].apply(lambda x: '{:,}'.format(x))
jj = jj.sort_values(by='AMT',ascending=False)
jj.index = range(1,len(jj)+1)
print(jj[['NAME','CITY','STATE','AMOUNT']].head(100))
print('\nTOTAL = ' + '{:,}'.format(sum(jj['AMT'])))


                                                  NAME             CITY STATE      AMOUNT
1                                    STEYER, THOMAS F.    SAN FRANCISCO    CA  15,743,487
2                              AMERICAN ACTION NETWORK       WASHINGTON    DC  15,290,970
3                                     UIHLEIN, RICHARD      LAKE FOREST    IL  13,229,800
4         UNITED BROTHERHOOD OF CARPENTERS AND JOINERS       WASHINGTON    DC   9,779,385
5                     REPUBLICAN GOVERNORS ASSOCIATION       WASHINGTON    DC   7,466,173
6               DEMOCRATIC GOVERNORS ASSOCIATION (DGA)       WASHINGTON    DC   7,177,000
7                                      WALL, KATHALEEN          HOUSTON    TX   6,000,557
8                                   AFT SOLIDARITY 527       WASHINGTON    DC   5,100,000
9                                       EYCHANER, FRED          CHICAGO    IL   4,825,300
10                                 UIHLEIN, RICHARD E.      LAKE FOREST    IL   4,761,200
11        

### Largest Individual Contributions Grouped by Committees Connected to Specific Candidates

In [52]:
jj = ii[pd.notnull(ii['CAND_ID'])]
jj = jj.groupby(['CMTE_NM','CAND_NAME','PARTY'])['AMT'].agg(['sum'])
jj = jj.reset_index(level=['CMTE_NM','CAND_NAME','PARTY'])
jj.columns = ['CMTE_NM','CAND_NAME','PARTY','AMT']
jj['AMOUNT'] = jj['AMT'].apply(lambda x: '{:,}'.format(x))
jj = jj.sort_values(by='AMT',ascending=False)
jj.index = range(1,len(jj)+1)
print(jj[['CMTE_NM','CAND_NAME','PARTY','AMOUNT']].head(100))
print('\nTOTAL = ' + '{:,}'.format(sum(jj['AMT'])))


                                          CMTE_NM                      CAND_NAME PARTY      AMOUNT
1                                       TEAM RYAN                  RYAN, PAUL D.   REP  47,635,251
2                 DOUG JONES FOR SENATE COMMITTEE                    JONES, DOUG   DEM  14,836,339
3                         MCCASKILL FOR MISSOURI               MCCASKILL, CLAIRE   DEM  12,290,297
4                         JON OSSOFF FOR CONGRESS            OSSOFF, T. JONATHAN   DEM  11,017,533
5                           GILLIBRAND FOR SENATE  GILLIBRAND, KIRSTEN ELIZABETH   DEM  10,349,232
6                           MCCARTHY VICTORY FUND                MCCARTHY, KEVIN   REP   9,578,875
7                        FRIENDS OF SHERROD BROWN                 BROWN, SHERROD   DEM   9,458,186
8                        TAMMY BALDWIN FOR SENATE                 BALDWIN, TAMMY   DEM   7,179,935
9                      BILL NELSON FOR U S SENATE                   NELSON, BILL   DEM   6,294,430
10        

### Largest Individual Contributions Grouped by Committees Not Connected to Specific Candidates

In [53]:
jj = ii[pd.isnull(ii['CAND_ID'])]
jj = jj.groupby(['CMTE_NM'])['AMT'].agg(['sum'])
jj = jj.reset_index(level=['CMTE_NM'])
jj.columns = ['CMTE_NM','AMT']
jj['AMOUNT'] = jj['AMT'].apply(lambda x: '{:,}'.format(x))
jj = jj.sort_values(by='AMT',ascending=False)
jj.index = range(1,len(jj)+1)
print(jj[['CMTE_NM','AMOUNT']].head(100))
print('\nTOTAL = ' + '{:,}'.format(sum(jj['AMT'])))


                                               CMTE_NM       AMOUNT
1                                              ACTBLUE  212,966,091
2                        REPUBLICAN NATIONAL COMMITTEE   64,402,263
3                                                 DCCC   49,638,981
4                        CONGRESSIONAL LEADERSHIP FUND   33,823,523
5                                                 DSCC   31,760,217
6              DNC SERVICES CORP./DEM. NAT'L COMMITTEE   28,985,242
7                                                 NRSC   23,231,331
8                                        TRUMP VICTORY   22,961,326
9                                                  SMP   21,891,530
10                                                NRCC   19,116,614
11                              SENATE LEADERSHIP FUND   18,082,700
12                    NEXTGEN CLIMATE ACTION COMMITTEE   16,040,073
13                                        EMILY'S LIST   12,850,885
14                                  HOUSE MAJORI

### Largest Individual Contributions Grouped by Candidates

In [54]:
jj = ii.groupby(['CAND_NAME','PARTY'])['AMT'].agg(['sum'])
jj = jj.reset_index(level=['CAND_NAME','PARTY'])
jj.columns = ['CAND_NAME','PARTY','AMT']
jj['AMOUNT'] = jj['AMT'].apply(lambda x: '{:,}'.format(x))
jj = jj.sort_values(by='AMT',ascending=False)
jj.index = range(1,len(jj)+1)
print(jj[['CAND_NAME','PARTY','AMOUNT']].head(100))
print('\nTOTAL = ' + '{:,}'.format(sum(jj['AMT'])))


                         CAND_NAME PARTY      AMOUNT
1                    RYAN, PAUL D.   REP  48,526,396
2                      JONES, DOUG   DEM  15,006,339
3                MCCASKILL, CLAIRE   DEM  12,757,572
4                   BROWN, SHERROD   DEM  12,275,426
5              OSSOFF, T. JONATHAN   DEM  11,017,533
6    GILLIBRAND, KIRSTEN ELIZABETH   DEM  10,837,981
7                  MCCARTHY, KEVIN   REP   9,928,647
8                   BALDWIN, TAMMY   DEM   8,245,775
9               CASEY, ROBERT P JR   DEM   7,162,817
10                    CORNYN, JOHN   REP   6,877,185
11                    NELSON, BILL   DEM   6,430,450
12         CRUZ, RAFAEL EDWARD TED   REP   6,043,705
13            WALL, KATHALEEN MRS.   REP   5,946,877
14         O'ROURKE, ROBERT (BETO)   DEM   5,370,099
15                STABENOW, DEBBIE   DEM   5,126,563
16                     FLAKE, JEFF   REP   4,952,431
17               SCALISE, STEVE MR   REP   4,622,876
18               WARREN, ELIZABETH   DEM   4,6

### For a Specified Contributor, List All Contributions to Committees
First, list all contributions to committees connected to specific candidates.
Then, list all contributions to committees not connected to specific candidates.


In [55]:
def getIndividual2Candidate(name, city, state):
    jj = ii[ii['NAME'].str.contains(name, na=False)]
    if pd.notnull(city): jj = jj[jj['CITY'].str.contains(city, na=False)]
    if pd.notnull(state): jj = jj[jj['STATE'].str.contains(state, na=False)]
    jj = jj[pd.notnull(jj['CAND_ID'])]
    jj['AMOUNT'] = jj['AMT'].apply(lambda x: '{:,}'.format(x))
    jj = jj.sort_values(by='DATE',ascending=True)
    jj.index = range(1,len(jj)+1)
    kk = jj[['NAME','DATE','AMOUNT','CITY','STATE','CAND_NAME','PARTY']]
    print(kk.head(100))
    print('\nSUBTOTAL = ' + '{:,}'.format(sum(jj['AMT'])))

def getIndividual2Committee(name, city, state):
    jj = ii[ii['NAME'].str.contains(name, na=False)]
    if pd.notnull(city): jj = jj[jj['CITY'].str.contains(city, na=False)]
    if pd.notnull(state): jj = jj[jj['STATE'].str.contains(state, na=False)]
    jj = jj[pd.isnull(jj['CAND_ID'])]
    jj['AMOUNT'] = jj['AMT'].apply(lambda x: '{:,}'.format(x))
    jj = jj.sort_values(by='DATE',ascending=True)
    jj.index = range(1,len(jj)+1)
    kk = jj[['NAME','DATE','AMOUNT','CITY','STATE','CMTE_NM']]
    print(kk.head(100))
    print('\nSUBTOTAL = ' + '{:,}'.format(sum(jj['AMT'])))

def getIndividual2All(name, city, state):
    getIndividual2Candidate(name, city, state)
    getIndividual2Committee(name, city, state)

#getIndividual2All('UIHLEIN, RICHARD')
getIndividual2All('KOCH,', None, 'KS')


                           NAME       DATE   AMOUNT     CITY STATE              CAND_NAME PARTY
1             KOCH, ELIZABETH B 2017-06-30    2,700  WICHITA    KS         HATCH, ORRIN G   REP
2             KOCH, ELIZABETH B 2017-06-30    2,700  WICHITA    KS         HATCH, ORRIN G   REP
3               KOCH, CHARLES G 2017-06-30    2,700  WICHITA    KS         HATCH, ORRIN G   REP
4               KOCH, CHARLES G 2017-06-30    2,700  WICHITA    KS         HATCH, ORRIN G   REP
5                   KOCH, JULIA 2017-07-17    2,700  WICHITA    KS          ZELDIN, LEE M   REP
6                   KOCH, JULIA 2017-07-17    2,300  WICHITA    KS          ZELDIN, LEE M   REP
7                   KOCH, DAVID 2017-07-19    2,700  WICHITA    KS          ZELDIN, LEE M   REP
8                   KOCH, DAVID 2017-07-19    2,300  WICHITA    KS          ZELDIN, LEE M   REP
9         KOCH, ELIZABETH BUZZI 2017-11-27    2,700  WICHITA    KS  BLACKBURN, MARSHA MRS   REP
10                KOCH, CHARLES 2017-11-

### For a Specified Committee, List All Individual Contributions

In [56]:
def getIndividual2Committee1(cmte_nm):
    jj = ii[ii['CMTE_NM'].str.contains(cmte_nm, na=False)]
    jj['AMOUNT'] = jj['AMT'].apply(lambda x: '{:,}'.format(x))
    jj = jj.sort_values(by='DATE',ascending=True)
    jj.index = range(1,len(jj)+1)
    kk = jj[['NAME','DATE','AMOUNT','CITY','STATE','CMTE_NM']]
    print(kk.head(100))
    print('\nSUBTOTAL = ' + '{:,}'.format(sum(jj['AMT'])))

getIndividual2Committee1('CROSSROAD')


                                  NAME       DATE     AMOUNT        CITY STATE              CMTE_NM
1            MCCORMICK, RICHARD D. MR. 2017-08-15     25,000      DENVER    CO  AMERICAN CROSSROADS
2               FRALIN, W. HEYWOOD MR. 2017-12-18     25,000     ROANOKE    VA  AMERICAN CROSSROADS
3  AGC CONSTRUCTION ADVOCACY FUND INC. 2017-12-21     25,000   ARLINGTON    VA  AMERICAN CROSSROADS
4     HILLWOOD DEVELOPMENT COMPANY LLC 2017-12-21  1,000,000      DALLAS    TX  AMERICAN CROSSROADS
5                      REEDER, KENNETH 2018-12-07        500  CINCINNATI    OH  AMERICAN CROSSROADS

SUBTOTAL = 1,075,500


C:\Users\bdavi\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


### For a Specified Candidate, List All Individual Contributions

In [58]:
def getIndividual2Candidate1(cand_name):
    jj = ii[ii['CAND_NAME'].str.contains(cand_name, na=False)]
    jj['AMOUNT'] = jj['AMT'].apply(lambda x: '{:,}'.format(x))
    jj = jj.sort_values(by='DATE',ascending=True)
    jj.index = range(1,len(jj)+1)
    kk = jj[['NAME','DATE','AMOUNT','CITY','STATE','CAND_NAME','PARTY']]
    print(kk.head(100))
    print('\nSUBTOTAL = ' + '{:,}'.format(sum(jj['AMT'])))

getIndividual2Candidate1('TRUMP')


                       NAME       DATE  AMOUNT                  CITY STATE        CAND_NAME PARTY
1           IJAMES, KEVIN M 2016-11-09   1,000              SULLIVAN    MO  TRUMP, DONALD J   REP
2              MACRI, FRANK 2016-11-30     250          PHILADELPHIA    PA  TRUMP, DONALD J   REP
3              TAMAYO, DINO 2016-11-30      30        EAST NORTHPORT    NY  TRUMP, DONALD J   REP
4           WEAVER, WILLIAM 2016-12-03     500          INDIANAPOLIS    IN  TRUMP, DONALD J   REP
5            LEMOINE, TAMMY 2016-12-09     250              MAUREPAS    LA  TRUMP, DONALD J   REP
6             HART, PATRICK 2016-12-09     100  PALOS VERDES ESTATES    CA  TRUMP, DONALD J   REP
7            BUETTNER, MARK 2016-12-17      59             DAVENPORT    IA  TRUMP, DONALD J   REP
8             BOWEN, MARTHA 2016-12-20      35           CATONSVILLE    MD  TRUMP, DONALD J   REP
9    GRIFFITH, JOSEPH P MR. 2016-12-29   1,000            CHARLESTON    SC  TRUMP, DONALD J   REP
10            DE PIL

C:\Users\bdavi\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until
